In [47]:
import scipy.stats as stats
import xarray
import numpy as np
import xarray
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
import geopandas as gpd
import pandas as pd
import folium

In [14]:
# time range: 1940-01 ~ 2022-12
all_data = xarray.open_dataset("workspaces/app_workspace/combined_all_data_101.nc")
all_data

<xarray.Dataset>
Dimensions:            (rivid: 38903, time: 996, variable: 3, nerr: 3)
Coordinates:
  * rivid              (rivid) int32 110229254 110230566 ... 110294992 110296304
    lon                (rivid) float64 ...
    lat                (rivid) float64 ...
  * time               (time) datetime64[ns] 1940-01-31 ... 2022-12-31
  * variable           (variable) <U8 'Qout' 'Qout_err' 'crs'
Dimensions without coordinates: nerr
Data variables:
    ds_grouped_avg     (variable, time, rivid, nerr) float64 ...
    ds_grouped_median  (variable, time, rivid, nerr) float64 ...

In [15]:
monthly_data = xarray.open_dataset("workspaces/app_workspace/combined_monthly_data.nc")
monthly_data

<xarray.Dataset>
Dimensions:          (rivid: 38903, month: 12, variable: 2)
Coordinates:
  * rivid            (rivid) int32 110229254 110230566 ... 110294992 110296304
    lon              (rivid) float64 ...
    lat              (rivid) float64 ...
  * month            (month) int64 1 2 3 4 5 6 7 8 9 10 11 12
  * variable         (variable) <U4 'Qout' 'crs'
Data variables:
    monthly_average  (variable, month, rivid) float64 ...
    monthly_std_dev  (variable, month, rivid) float64 ...

In [32]:
month_num = 10
year_num = 2010

In [50]:
# Filter data directly in xarray
filtered_data = all_data["ds_grouped_avg"].sel(
    variable="Qout",
    time=(all_data["ds_grouped_avg"]["time"].dt.month == month_num) &
         (all_data["ds_grouped_avg"]["time"].dt.year == year_num)
)
filtered_data

<xarray.DataArray 'ds_grouped_avg' (time: 1, rivid: 38903, nerr: 3)>
[116709 values with dtype=float64]
Coordinates:
  * rivid     (rivid) int32 110229254 110230566 ... 110294992 110296304
    lon       (rivid) float64 ...
    lat       (rivid) float64 ...
  * time      (time) datetime64[ns] 2010-10-31
    variable  <U8 'Qout'
Dimensions without coordinates: nerr
Attributes:
    Conventions:  CF-1.6
    title:        
    institution:  
    source:       RAPID: unknown, NOT a git repository, water inflow: /mnt/in...
    history:      date_created: 2023-10-26T14:31:52+00:00
    references:   https://github.com/c-h-david/rapid/, http://dx.doi.org/10.1...
    comment:      
    featureType:  timeSeries

In [49]:
filtered_data

<xarray.DataArray 'ds_grouped_avg' (time: 1, rivid: 38903, nerr: 3)>
array([[[7.266409e-02, 7.266409e-02, 7.266409e-02],
        [2.740042e-02, 2.740042e-02, 2.740042e-02],
        ...,
        [4.190606e+01, 4.190606e+01, 4.190606e+01],
        [4.203548e+01, 4.203548e+01, 4.203548e+01]]])
Coordinates:
  * rivid     (rivid) int32 110229254 110230566 ... 110294992 110296304
    lon       (rivid) float64 ...
    lat       (rivid) float64 ...
  * time      (time) datetime64[ns] 2010-10-31
    variable  <U8 'Qout'
Dimensions without coordinates: nerr
Attributes:
    Conventions:  CF-1.6
    title:        
    institution:  
    source:       RAPID: unknown, NOT a git repository, water inflow: /mnt/in...
    history:      date_created: 2023-10-26T14:31:52+00:00
    references:   https://github.com/c-h-david/rapid/, http://dx.doi.org/10.1...
    comment:      
    featureType:  timeSeries

In [51]:
# Convert the filtered data to a DataFrame
# TODO what is nerr?
month_df = filtered_data.to_dataframe().reset_index()
month_df

time      rivid  nerr        lon        lat variable  \
0      2010-10-31  110229254     0  34.699222  -5.514889     Qout   
1      2010-10-31  110229254     1  34.699222  -5.514889     Qout   
2      2010-10-31  110229254     2  34.699222  -5.514889     Qout   
3      2010-10-31  110230566     0  34.718444  -5.503333     Qout   
4      2010-10-31  110230566     1  34.718444  -5.503333     Qout   
...           ...        ...   ...        ...        ...      ...   
116704 2010-10-31  110294992     1  40.360556 -10.570000     Qout   
116705 2010-10-31  110294992     2  40.360556 -10.570000     Qout   
116706 2010-10-31  110296304     0  40.432778 -10.471556     Qout   
116707 2010-10-31  110296304     1  40.432778 -10.471556     Qout   
116708 2010-10-31  110296304     2  40.432778 -10.471556     Qout   

        ds_grouped_avg  
0             0.072664  
1             0.072664  
2             0.072664  
3             0.027400  
4             0.027400  
...                ...  
116704       41.906059  
116705       41.906059  
116706       42.035480  
116707       42.035480  
116708       42.035480  

[116709 rows x 7 columns]

In [35]:
print(filtered_data.shape)

(1, 38903, 3)


In [19]:
average_df = monthly_data["monthly_average"].to_dataframe().reset_index()
average_df = average_df[(average_df["variable"] == "Qout") & (average_df["month"] == month_num)]
std_df = monthly_data["monthly_std_dev"].to_dataframe().reset_index()
std_df = std_df[(std_df["variable"] == "Qout") & (std_df["month"] == month_num)]
merged_df = month_df.merge(average_df[['rivid', 'monthly_average']], on='rivid', how='left')
merged_df = merged_df.merge(std_df[['rivid', 'monthly_std_dev']], on='rivid', how='left')
merged_df

time      rivid  nerr        lon        lat variable  \
0      2010-01-31  110229254     0  34.699222  -5.514889     Qout   
1      2010-01-31  110229254     1  34.699222  -5.514889     Qout   
2      2010-01-31  110229254     2  34.699222  -5.514889     Qout   
3      2010-01-31  110230566     0  34.718444  -5.503333     Qout   
4      2010-01-31  110230566     1  34.718444  -5.503333     Qout   
...           ...        ...   ...        ...        ...      ...   
116704 2010-01-31  110294992     1  40.360556 -10.570000     Qout   
116705 2010-01-31  110294992     2  40.360556 -10.570000     Qout   
116706 2010-01-31  110296304     0  40.432778 -10.471556     Qout   
116707 2010-01-31  110296304     1  40.432778 -10.471556     Qout   
116708 2010-01-31  110296304     2  40.432778 -10.471556     Qout   

        ds_grouped_avg  monthly_average  monthly_std_dev  
0             1.447822         1.291060         0.635615  
1             1.447822         1.291060         0.635615  
2             1.447822         1.291060         0.635615  
3             1.187610         1.177018         0.729382  
4             1.187610         1.177018         0.729382  
...                ...              ...              ...  
116704     1358.473633      1582.733887       914.329407  
116705     1358.473633      1582.733887       914.329407  
116706     1352.632324      1574.041382       911.089661  
116707     1352.632324      1574.041382       911.089661  
116708     1352.632324      1574.041382       911.089661  

[116709 rows x 9 columns]

In [20]:
# Calculate Z-score for ds_grouped_avg using mean and standard deviation
merged_df['z_score'] = (merged_df['ds_grouped_avg'] - merged_df['monthly_average']) / merged_df['monthly_std_dev']

# Calculate exceedance probability using the cumulative distribution function (CDF)
merged_df['probability'] = stats.norm.cdf(merged_df['z_score'])
merged_df

time      rivid  nerr        lon        lat variable  \
0      2010-01-31  110229254     0  34.699222  -5.514889     Qout   
1      2010-01-31  110229254     1  34.699222  -5.514889     Qout   
2      2010-01-31  110229254     2  34.699222  -5.514889     Qout   
3      2010-01-31  110230566     0  34.718444  -5.503333     Qout   
4      2010-01-31  110230566     1  34.718444  -5.503333     Qout   
...           ...        ...   ...        ...        ...      ...   
116704 2010-01-31  110294992     1  40.360556 -10.570000     Qout   
116705 2010-01-31  110294992     2  40.360556 -10.570000     Qout   
116706 2010-01-31  110296304     0  40.432778 -10.471556     Qout   
116707 2010-01-31  110296304     1  40.432778 -10.471556     Qout   
116708 2010-01-31  110296304     2  40.432778 -10.471556     Qout   

        ds_grouped_avg  monthly_average  monthly_std_dev   z_score  \
0             1.447822         1.291060         0.635615  0.246630   
1             1.447822         1.291060         0.635615  0.246630   
2             1.447822         1.291060         0.635615  0.246630   
3             1.187610         1.177018         0.729382  0.014522   
4             1.187610         1.177018         0.729382  0.014522   
...                ...              ...              ...       ...   
116704     1358.473633      1582.733887       914.329407 -0.245273   
116705     1358.473633      1582.733887       914.329407 -0.245273   
116706     1352.632324      1574.041382       911.089661 -0.243016   
116707     1352.632324      1574.041382       911.089661 -0.243016   
116708     1352.632324      1574.041382       911.089661 -0.243016   

        probability  
0          0.597403  
1          0.597403  
2          0.597403  
3          0.505793  
4          0.505793  
...             ...  
116704     0.403123  
116705     0.403123  
116706     0.403997  
116707     0.403997  
116708     0.403997  

[116709 rows x 11 columns]

In [21]:
# Assuming 'merged_df' is your DataFrame
# Replace 'lat', 'lon', and 'exceedance_probability' with your actual column names

# Define the categories and corresponding colors
categories = ["extremely dry", "dry", "normal range", "wet", "extremely wet"]
colors = ["#CD233F", "#FFA885", "#E7E2BC", "#8ECEEE", "#2C7DCD"]

category_colors = {
    "extremely dry": "#CD233F",
    "dry": "#FFA885",
    "normal range": "#E7E2BC",
    "wet": "#8ECEEE",
    "extremely wet": "#2C7DCD"
}

# Map the exceedance_probability values to categories
merged_df['classification'] = np.select(
    [merged_df['probability'] >= 0.87,
     (merged_df['probability'] >= 0.72) & (merged_df['probability'] < 0.87),
     (merged_df['probability'] >= 0.28) & (merged_df['probability'] < 0.72),
     (merged_df['probability'] >= 0.13) & (merged_df['probability'] < 0.28),
     merged_df['probability'] < 0.13],
    categories, default="unknown"
)

merged_df

time      rivid  nerr        lon        lat variable  \
0      2010-01-31  110229254     0  34.699222  -5.514889     Qout   
1      2010-01-31  110229254     1  34.699222  -5.514889     Qout   
2      2010-01-31  110229254     2  34.699222  -5.514889     Qout   
3      2010-01-31  110230566     0  34.718444  -5.503333     Qout   
4      2010-01-31  110230566     1  34.718444  -5.503333     Qout   
...           ...        ...   ...        ...        ...      ...   
116704 2010-01-31  110294992     1  40.360556 -10.570000     Qout   
116705 2010-01-31  110294992     2  40.360556 -10.570000     Qout   
116706 2010-01-31  110296304     0  40.432778 -10.471556     Qout   
116707 2010-01-31  110296304     1  40.432778 -10.471556     Qout   
116708 2010-01-31  110296304     2  40.432778 -10.471556     Qout   

        ds_grouped_avg  monthly_average  monthly_std_dev   z_score  \
0             1.447822         1.291060         0.635615  0.246630   
1             1.447822         1.291060         0.635615  0.246630   
2             1.447822         1.291060         0.635615  0.246630   
3             1.187610         1.177018         0.729382  0.014522   
4             1.187610         1.177018         0.729382  0.014522   
...                ...              ...              ...       ...   
116704     1358.473633      1582.733887       914.329407 -0.245273   
116705     1358.473633      1582.733887       914.329407 -0.245273   
116706     1352.632324      1574.041382       911.089661 -0.243016   
116707     1352.632324      1574.041382       911.089661 -0.243016   
116708     1352.632324      1574.041382       911.089661 -0.243016   

        probability classification  
0          0.597403   normal range  
1          0.597403   normal range  
2          0.597403   normal range  
3          0.505793   normal range  
4          0.505793   normal range  
...             ...            ...  
116704     0.403123   normal range  
116705     0.403123   normal range  
116706     0.403997   normal range  
116707     0.403997   normal range  
116708     0.403997   normal range  

[116709 rows x 12 columns]

In [29]:
gdf = gpd.GeoDataFrame(merged_df, geometry=gpd.points_from_xy(merged_df.lat, merged_df.lon))
gdf = gdf.drop_duplicates(["rivid"])
gdf["time"] = gdf["time"].astype(str)
gdf = gdf.reset_index()
gdf

index        time      rivid  nerr        lon        lat variable  \
0           0  2010-01-31  110229254     0  34.699222  -5.514889     Qout   
1           3  2010-01-31  110230566     0  34.718444  -5.503333     Qout   
2           6  2010-01-31  110067878     0  34.740778  -5.522000     Qout   
3           9  2010-01-31  110050823     0  34.560222  -5.538111     Qout   
4          12  2010-01-31  110054759     0  34.560222  -5.538111     Qout   
...       ...         ...        ...   ...        ...        ...      ...   
38898  116694  2010-01-31  110308113     0  40.277556 -10.585000     Qout   
38899  116697  2010-01-31  110292368     0  40.288889 -10.584111     Qout   
38900  116700  2010-01-31  110293680     0  40.351778 -10.577222     Qout   
38901  116703  2010-01-31  110294992     0  40.360556 -10.570000     Qout   
38902  116706  2010-01-31  110296304     0  40.432778 -10.471556     Qout   

       ds_grouped_avg  monthly_average  monthly_std_dev   z_score  \
0            1.447822         1.291060         0.635615  0.246630   
1            1.187610         1.177018         0.729382  0.014522   
2            1.294694         1.237655         0.842541  0.067699   
3            0.899028         0.675618         0.669494  0.333699   
4            2.338089         1.665455         2.777421  0.242179   
...               ...              ...              ...       ...   
38898     1359.496338      1582.141113       914.681091 -0.243412   
38899     1359.110596      1581.514160       914.454590 -0.243209   
38900     1357.895874      1581.969604       914.241028 -0.245093   
38901     1358.473633      1582.733887       914.329407 -0.245273   
38902     1352.632324      1574.041382       911.089661 -0.243016   

       probability classification                    geometry  
0         0.597403   normal range   POINT (-5.51489 34.69922)  
1         0.505793   normal range   POINT (-5.50333 34.71844)  
2         0.526987   normal range   POINT (-5.52200 34.74078)  
3         0.630697   normal range   POINT (-5.53811 34.56022)  
4         0.595679   normal range   POINT (-5.53811 34.56022)  
...            ...            ...                         ...  
38898     0.403843   normal range  POINT (-10.58500 40.27756)  
38899     0.403922   normal range  POINT (-10.58411 40.28889)  
38900     0.403192   normal range  POINT (-10.57722 40.35178)  
38901     0.403123   normal range  POINT (-10.57000 40.36056)  
38902     0.403997   normal range  POINT (-10.47156 40.43278)  

[38903 rows x 14 columns]

In [31]:
gdf[["rivid", "classification", "geometry"]].to_json()

'{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {"rivid": 110229254, "classification": "normal range"}, "geometry": {"type": "Point", "coordinates": [-5.514888888884329, 34.699222222221685]}}, {"id": "1", "type": "Feature", "properties": {"rivid": 110230566, "classification": "normal range"}, "geometry": {"type": "Point", "coordinates": [-5.503333333328769, 34.718444444443904]}}, {"id": "2", "type": "Feature", "properties": {"rivid": 110067878, "classification": "normal range"}, "geometry": {"type": "Point", "coordinates": [-5.521999999995437, 34.74077777777723]}}, {"id": "3", "type": "Feature", "properties": {"rivid": 110050823, "classification": "normal range"}, "geometry": {"type": "Point", "coordinates": [-5.538111111106545, 34.560222222221704]}}, {"id": "4", "type": "Feature", "properties": {"rivid": 110054759, "classification": "normal range"}, "geometry": {"type": "Point", "coordinates": [-5.538111111106545, 34.560222222221704]}}, {"id": 

In [24]:
gdf = gdf.drop_duplicates(["rivid"])
gdf["time"] = gdf["time"].astype(str)
gdf[["rivid", "classification", "geometry"]].to_file("public/data/geojson/hydrosos_streamflow_output.geojson", driver="GeoJSON")

/home/ysun/miniconda3/envs/tethys/lib/python3.11/site-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [25]:
m = folium.Map(location=[0, 0], zoom_start=2, tiles="cartodbpositron")
for index, row in gdf.iterrows():
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=5,
        color='gray',
        fill=True,
        fill_color=category_colors[row['category']],
        fill_opacity=0.7,
        weight=0.5
        # popup=row['category']
    ).add_to(m)
m

KeyError: 'category'

In [36]:
year = 2010
month = 10
app_workspace_dir = "workspaces/app_workspace"
all_data = xarray.open_dataset(f"{app_workspace_dir}/combined_all_data_101.nc")
monthly_data = xarray.open_dataset(f"{app_workspace_dir}/combined_monthly_data.nc")
filtered_data = all_data["ds_grouped_avg"].sel(
    variable="Qout",
    time=(all_data["ds_grouped_avg"]["time"].dt.month == month) &
        (all_data["ds_grouped_avg"]["time"].dt.year == year)
)
print("the dimension of the filtered data:", filtered_data.shape)

the dimension of the filtered data: (1, 38903, 3)
